In [35]:
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from concurrent.futures import ProcessPoolExecutor, ThreadPoolExecutor
from itertools import combinations
import pandas as pd
import warnings
import json
import re

image_path = 'C:/Users/tabm9/OneDrive - Caissa Analytica/Documents/DS_Portfolio/Projects/Images/RLCS/'

In [52]:
def write_plot(fig: go.Figure, file_name: str, path: str = image_path, **kwargs):
    # Transform into html
    html = fig.to_html(include_plotlyjs='cdn', div_id=file_name, **kwargs)

    # Extract js code
    js_start = [s.end() for s in re.finditer('<script type="text/javascript">', html)][-1]
    js_end = [s.start() for s in re.finditer('</script>', html)][-1]

    js = html[js_start: js_end]

    # # Extract div
    # html = html[html.find('<div id'): html.find('</div>') + 6]

    # Write files
    with open(path + file_name + '.js', 'w') as f:
        f.write(js)

    # with open(path + file_name + '.html', 'w') as f:
    #     f.write(html)

    # return html

line_color = '#f1f5f9'
font_color = '#f1f5f9'
background_color = '#032137'

layout_dict = dict(
    font_color=font_color,
    paper_bgcolor='rgba(0,0,0,0)',
    plot_bgcolor='rgba(0,0,0,0)',
    xaxis = dict(gridcolor=line_color, linecolor=line_color, zerolinecolor=line_color),
    yaxis = dict(gridcolor=line_color, linecolor=line_color, zerolinecolor=line_color),
    legend=dict(x=0, y=1, bgcolor=background_color),
    margin=dict(r=0, l=0, b=0)
)

tablet_args = dict(default_width='700px', default_height='300px')
mobile_args = dict(default_width='400px', default_height='175px')

In [37]:
def bound_array(a, bounds=[0, 1]):
    s = a.copy()

    # Check number of times it breaks bounds
    signed_crosses = np.floor((s - bounds[0]) / (bounds[1] - bounds[0])).astype(int)
    crosses = np.floor(np.where(signed_crosses < 0, -signed_crosses, signed_crosses)).astype(int)

    # Reorient direction
    s *= ((-1) ** crosses)

    # Reposition to maintain continuity
    s += (bounds[1] - bounds[0]) * signed_crosses * (-1) ** (crosses + 1)
    s += (bounds[1] + bounds[0]) * 0 ** ((crosses + 1) % 2)

    return s


def bounded_random_walk(initial=1/2, bounds=[0, 1], size=[1000, 10], drift=0, std=0.007, is_deterministic=False):
    if is_deterministic: return np.ones(size) * initial

    # Generate random walk initialized on 0
    walk = np.random.normal(loc=drift, scale=std, size=size).cumsum(0) + initial

    # Adjust walk to bounds
    walk = bound_array(walk, bounds)        

    return walk

fig = go.Figure(layout=layout_dict)

walks = bounded_random_walk().T

for walk in walks:
    fig.add_trace(go.Scatter(y=walk, opacity=0.5, showlegend=False))

fig.update_yaxes(range=[0, 1])
fig.show()

# Test with only 2 teams

## Naive Elo

In [38]:
def run_games(Pa=1/4, K=1, N=[10000, 1], thres=0.10, stop_burnout=False, is_deterministic=True):
    # Run N games
    Ps = bounded_random_walk(initial=Pa, size=N, is_deterministic=is_deterministic)
    Sa = (np.random.random(N) < Ps).astype(int)

    # Calculate Ratings
    Ra = np.zeros(N)
    pa = np.zeros(N)
    pa[0] += 1/2
    finished_burnout = np.array([False] * N[1])
    n_to_convergence = np.ones(N[1]) * (N[0] + 1)
    for i in range(1, N[0]):
        # Update rating
        Ra[i] = Ra[i-1] + K * (Sa[i - 1] - pa[i - 1])

        # Update Approx Probabilities
        pa[i] = 1 / (1 + 10 ** (-2 * Ra[i] / 400))

        # Check if burnout is finished
        if not all(finished_burnout):
            condition = abs(pa[i] - Ps[i]) <= Ps[i] * thres
            finished_burnout = np.where(condition, True, finished_burnout)
            n_to_convergence = np.where(finished_burnout, n_to_convergence, i + 1)

            if all(finished_burnout) and stop_burnout:
                break

    return abs(Ps - pa).T, n_to_convergence


## Improved Elo

In [39]:
def logbase(base, x):
    return np.log(x) / np.log(base)

def K_generator(K_interval=[0,400], K_default=300):
    K_d = (K_default - K_interval[0]) / (K_interval[1] - K_interval[0])
    b = logbase(1/2, 1/2 - np.log((1 + np.e ** (-2 * np.e) - K_d) / (K_d + np.e ** (-2 * np.e))) / (4 * np.e))

    def K_function(x, b=b, K_interval=K_interval):
        return (K_interval[1] - K_interval[0]) * ((1 + 2 * np.e ** (-2 * np.e)) / (1 + np.e ** (-4 * np.e * (x ** b - 1/2))) - np.e ** (-2 * np.e)) + K_interval[0]

    return K_function



def run_games_improved(Pa=1/4, K_interval=[0,200], K_default=180, N=[10000, 1], thres=0.10, thres_n=10, window=100, stop_burnout=False, is_deterministic=True):
    # Run N games
    Ps = bounded_random_walk(initial=Pa, size=N, is_deterministic=is_deterministic)
    Sa = (np.random.random(N) < Ps).astype(int)

    # Calculate Ratings
    Ra = np.zeros(N)
    pa = np.zeros(N)
    pa[0] += 1/2
    fpa_list = pa.copy()
    finished_burnout = np.array([False] * N[1])
    n_to_convergence = np.ones(N[1]) * (N[0] + 1)
    K = K_generator(K_interval=K_interval, K_default=K_default)
    K_list = -np.ones(N)

    for i in range(1, N[0]):
        # Update rating
        frequentist_pa = Sa[max(0, i - window):min(N[0], i + window)].mean(0)
        
        K_i = K(abs(pa[i - 1] - frequentist_pa))
        Ra[i] = Ra[i-1] + K_i * (Sa[i - 1] - pa[i - 1])

        K_list[i] = K_i
        fpa_list[i] = frequentist_pa

        # Update Approx Probabilities
        pa[i] = 1 / (1 + 10 ** (-2 * Ra[i] / 400))

        # Check if burnout is finished
        if not all(finished_burnout) and i >= thres_n:
            condition = (abs(pa[i - thres_n: i] - Ps[i - thres_n: i]) <= Ps[i - thres_n: i].mean() * thres).T.all(1)
            finished_burnout = np.where(condition, True, finished_burnout)
            n_to_convergence = np.where(finished_burnout, n_to_convergence, i + 1 - thres_n)

            if all(finished_burnout) and stop_burnout:
                break

    return abs(Ps - pa).T, n_to_convergence, fpa_list.T

## Comparison with static probabilities

In [53]:
# Setup parameters
Pa = 1/4
N_pa = [1000, 100]
N_conv = [3000, 10000]
N_range_pa = list(range(N_pa[0] + 1))

# Simulation
pa, _ = run_games(Pa=Pa, N=N_pa)
pa_improved, _, _ = run_games_improved(Pa=Pa, N=N_pa)

_, n_to_convergence = run_games(Pa=Pa, N=N_conv, stop_burnout=True)
_, n_to_convergence_improved, fpa_list = run_games_improved(Pa=Pa, N=N_conv, stop_burnout=True)


# Initialize plot
fig = make_subplots(
    rows = 2, 
    subplot_titles=('Actual vs. Approximated Probabilities Difference', 'Time to Convergence Distributions')
)

# Calculate quantiles
naive_quantiles = np.quantile(pa.T, [0.1, 0.5, 0.9], axis=1)
improved_quantiles = np.quantile(pa_improved.T, [0.1, 0.5, 0.9], axis=1)

# Add Probability lines
x_range = list(range(N_pa[0])) + list(reversed(range(N_pa[0])))

fig.add_trace(go.Scatter(
        x = x_range, y=list(naive_quantiles[2]) + list(naive_quantiles[0][::-1]), fill='toself', mode='none',
        hoveron='points', fillcolor='blue', name=f'Naive Probabilities', legendgroup=0, opacity=0.5
    ), row=1, col=1)
fig.add_trace(go.Scatter(y=naive_quantiles[1], line=dict(color='blue'), showlegend=False, legendgroup=0, name='Naive (Median)'), row=1, col=1)


fig.add_trace(go.Scatter(
        x = x_range, y=list(improved_quantiles[2]) + list(improved_quantiles[0][::-1]), fill='toself', mode='none',
        hoveron='points', fillcolor='red', name=f'Improved Probabilities', legendgroup=1, opacity=0.5
    ), row=1, col=1)
fig.add_trace(go.Scatter(y=improved_quantiles[1], line=dict(color='red'), showlegend=False, legendgroup=1, name='Improved (Median)'), row=1, col=1)

# Prepare histogram parameters
bin_width = 50
bins = list(range(0, int(np.ceil(max(max(n_to_convergence), max(n_to_convergence_improved)))), bin_width))

x_naive = np.mean(n_to_convergence)
y_naive = sum(np.digitize(n_to_convergence, bins) == np.digitize(x_naive, bins)) / N_conv[1]
x_improved = np.mean(n_to_convergence_improved)
y_improved = sum(np.digitize(n_to_convergence_improved, bins) == np.digitize(x_improved, bins)) / N_conv[1]

# Add histograms
fig.add_trace(go.Histogram(histnorm='probability', x=n_to_convergence, xbins=dict(size=bin_width), opacity=0.5, showlegend=False), row=2, col=1)
fig.add_trace(go.Histogram(histnorm='probability', x=n_to_convergence_improved, xbins=dict(size=bin_width), opacity=0.5, showlegend=False), row=2, col=1)

fig.add_annotation(x=x_naive, y=y_naive, xref='x2', yref='y2', text='Naive Elo', ax=50)
fig.add_annotation(x=x_improved, y=y_improved, xref='x2', yref='y2', text='Improved Elo', ax=50)

# Update Layout
fig.update_layout(barmode='overlay', title='Test with 2 Teams, Static Probabilities', **layout_dict)
fig.update_xaxes(title_text='Iteration', row=1, col=1)
fig.update_xaxes(title_text='Iteration', row=2, col=1)
fig.update_yaxes(title_text='Probability', range=[0, 1], row=1, col=1)
fig.update_yaxes(title_text='Probability', row=2, col=1)

# Show / save figure
fig.update_yaxes(range=[0, 1])
fig.show()
# fig.write_html(image_path + '2_Teams_Static_Probability.html')

## Comparison with Bounded Random Walk

In [54]:
# Setup parameters
Pa = 1/4
N_pa = [3000, 100]
N_conv = [3000, 10000]
N_range_pa = list(range(N_pa[0] + 1))

# Simulation
pa, _ = run_games(Pa=Pa, N=N_pa, is_deterministic=False)
pa_improved, _, _ = run_games_improved(Pa=Pa, N=N_pa, is_deterministic=False)

_, n_to_convergence = run_games(Pa=Pa, N=N_conv, is_deterministic=False, stop_burnout=True)
_, n_to_convergence_improved, fpa_list = run_games_improved(Pa=Pa, N=N_conv, is_deterministic=False, stop_burnout=True)


# Initialize plot
fig = make_subplots(
    rows = 2, 
    subplot_titles=('Actual vs. Approximated Probabilities', 'Time to Convergence Distributions')
)

# Calculate quantiles
naive_quantiles = np.quantile(pa.T, [0.1, 0.5, 0.9], axis=1)
improved_quantiles = np.quantile(pa_improved.T, [0.1, 0.5, 0.9], axis=1)

# Add Probability lines
x_range = list(range(N_pa[0])) + list(reversed(range(N_pa[0])))

fig.add_trace(go.Scatter(
        x = x_range, y=list(naive_quantiles[2]) + list(naive_quantiles[0][::-1]), fill='toself', mode='none',
        hoveron='points', fillcolor='blue', name=f'Naive Probabilities', legendgroup=0, opacity=0.5
    ), row=1, col=1)
fig.add_trace(go.Scatter(y=naive_quantiles[1], line=dict(color='blue'), showlegend=False, legendgroup=0, name='Naive (Median)'), row=1, col=1)


fig.add_trace(go.Scatter(
        x = x_range, y=list(improved_quantiles[2]) + list(improved_quantiles[0][::-1]), fill='toself', mode='none',
        hoveron='points', fillcolor='red', name=f'Improved Probabilities', legendgroup=1, opacity=0.5
    ), row=1, col=1)
fig.add_trace(go.Scatter(y=improved_quantiles[1], line=dict(color='red'), showlegend=False, legendgroup=1, name='Improved (Median)'), row=1, col=1)

# Prepare histogram parameters
bin_width = 50
bins = list(range(0, int(np.ceil(max(max(n_to_convergence), max(n_to_convergence_improved)))), bin_width))

x_naive = np.mean(n_to_convergence)
y_naive = sum(np.digitize(n_to_convergence, bins) == np.digitize(x_naive, bins)) / N_conv[1]
x_improved = np.mean(n_to_convergence_improved)
y_improved = sum(np.digitize(n_to_convergence_improved, bins) == np.digitize(x_improved, bins)) / N_conv[1]

# Add histograms
fig.add_trace(go.Histogram(histnorm='probability', x=n_to_convergence, xbins=dict(size=bin_width), opacity=0.5, showlegend=False), row=2, col=1)
fig.add_trace(go.Histogram(histnorm='probability', x=n_to_convergence_improved, xbins=dict(size=bin_width), opacity=0.5, showlegend=False), row=2, col=1)

fig.add_annotation(x=x_naive, y=y_naive, xref='x2', yref='y2', text='Naive Elo', ax=50)
fig.add_annotation(x=x_improved, y=y_improved, xref='x2', yref='y2', text='Improved Elo', ax=50)

# Update Layout
fig.update_layout(barmode='overlay', title='Test with 2 Teams, Bounded Random Walks', **layout_dict)
fig.update_xaxes(title_text='Iteration', row=1, col=1)
fig.update_xaxes(title_text='Iteration', row=2, col=1)
fig.update_yaxes(title_text='Probability', range=[0, 1], row=1, col=1)
fig.update_yaxes(title_text='Probability', row=2, col=1)

# Show / save figure
fig.update_yaxes(range=[0, 1])
fig.show()
# fig.write_html(image_path + '2_Teams_Bounded_Random_Walks.html')

# Test with 3 teams and stable process

$ P = \frac{1}{1 + a^{b \cdot D}} \rightarrow P_{AC} = \frac{1}{1 + \left[1 - \frac{1}{P_{AB}} \right] \cdot \left[1 - \frac{1}{P_{BC}} \right]} $

$ P = (1/2)^{y^{z \cdot D}} \rightarrow P_{AC} = P_{AB}^{log_{1/2}(P_{BC})} = P_{BC}^{log_{1/2}(P_{AB})} $

In [55]:
def calculate_implicit(p1, p2):
    return p1 ** (np.log(p2) / np.log(1/2))

P_1_beats_2 = bounded_random_walk(size=1000)
P_2_beats_3 = bounded_random_walk(size=1000)
P_1_beats_3	= 1 / (1 + (1 - 1 / P_1_beats_2) * (1 - 1 / P_2_beats_3))

fig = go.Figure(layout=layout_dict)

fig.add_trace(go.Scatter(y=P_1_beats_2, name='Probability 1 beats 2'))
fig.add_trace(go.Scatter(y=P_2_beats_3, name='Probability 2 beats 3'))
fig.add_trace(go.Scatter(y=P_1_beats_3, name=f'Implicit Probability 1 beats 3 (sigmoid)'))
fig.add_trace(go.Scatter(y=calculate_implicit(P_1_beats_2, P_2_beats_3), name=f'Implicit Probability 1 beats 3 (exp)'))
fig.add_trace(go.Scatter(y=calculate_implicit(P_2_beats_3, P_1_beats_2), name=f'Implicit Probability 1 beats 3 (exp inv)'))

fig.show()

In [56]:
def calculate_implicit_probability(P_A_beats_B, P_B_beats_C, weights_AB=1, weights_BC=1):
    weights = weights_AB + weights_BC
    with warnings.catch_warnings():
        warnings.simplefilter("ignore", category=RuntimeWarning)
        weighted_P_AB = (1 / P_A_beats_B - 1) ** (weights_AB / weights)
        weighted_P_BC = (1 / P_B_beats_C - 1) ** (weights_BC / weights)
    return 1 / (1 + weighted_P_AB * weighted_P_BC)

def stable_three_player_generator(N=[10000, 1], initials=[1/2, 1/2]):
    # Set probabilities
    P_1_beats_2 = bounded_random_walk(initial=initials[0], size=N)
    P_2_beats_3 = bounded_random_walk(initial=initials[1], size=N)
    P_1_beats_3 = calculate_implicit_probability(P_1_beats_2, P_2_beats_3)

    # Generate order of games
    games_players = np.random.choice([0, 1, 2], size=N)

    # Generate results
    games_results = np.random.random(N)
    p = np.array([P_1_beats_2, P_1_beats_3, P_2_beats_3])
    games_results = (games_results <= np.choose(games_players, p)).astype(int)

    return p, games_players, games_results

def calculate_weighted_probability(P_A_beats_B, P_A_beats_C, P_B_beats_C, weights_AB, weights_AC, weights_BC):
    weights = weights_AB + weights_AC + weights_BC
    
    with warnings.catch_warnings():
        warnings.simplefilter("ignore", category=RuntimeWarning)
        prob = P_A_beats_C * weights_AC 
        prob += calculate_implicit_probability(P_A_beats_B, P_B_beats_C, weights_AB, weights_BC) * (weights_AB + weights_BC)
        prob /= weights

    weird_cases = (P_A_beats_B == 0) | (P_A_beats_B == 1) | (P_B_beats_C == 0) | (P_B_beats_C == 1)
    return np.where(weird_cases, P_A_beats_C, prob)



def three_player_heuristic(games_players, games_results):
    games_choices = np.unique(games_players)

    averages = []
    counts = []
    for i in games_choices:
        games_choice_results = np.where(games_players == games_choices[i], games_results, np.nan)
        with warnings.catch_warnings():
            warnings.simplefilter("ignore", category=RuntimeWarning)
            averages.append(np.nanmean(games_choice_results, axis=0))
            counts.append(np.count_nonzero(~np.isnan(games_choice_results), axis=0))

    averages = np.array(averages)
    counts = np.array(counts)

    return np.array([
        # P that 0 beats 1
        calculate_weighted_probability(averages[1], averages[0], 1 - averages[2], counts[1], counts[0], counts[2]),
        # P that 0 beats 2
        calculate_weighted_probability(averages[0], averages[1], averages[2], counts[0], counts[1], counts[2]),
        # P that 1 beats 2
        calculate_weighted_probability(1 - averages[0], averages[2], averages[1], counts[0], counts[2], counts[1])
    ])

def calculate_probability(R_A, R_B):
    # Probability that A beats B
    return 1 / (1 + 10 ** ((R_B - R_A) / 400))

In [57]:
N = [1000, 1]
p, games_players, games_results = stable_three_player_generator(N=N)

window = 50

pa = []
for i in range(N[0]):
    games_players_i = games_players[max(0, i - window):min(N[0], i + window)]
    games_results_i = games_results[max(0, i - window):min(N[0], i + window)]
    pa.append(three_player_heuristic(games_players_i, games_results_i))
pa = np.array(pa)

fig = go.Figure(layout=layout_dict)

fig.add_trace(go.Scatter(y=p[0].flatten(), line=dict(color='blue'), name='A beats B', legendgroup=0))
fig.add_trace(go.Scatter(y=pa.T[0][0].flatten(), line=dict(color='blue'), opacity=0.5, showlegend=False, legendgroup=0))

fig.add_trace(go.Scatter(y=p[1].flatten(), line=dict(color='red'), name='A beats C', legendgroup=1))
fig.add_trace(go.Scatter(y=pa.T[0][1].flatten(), line=dict(color='red'), opacity=0.5, showlegend=False, legendgroup=1))

fig.add_trace(go.Scatter(y=p[2].flatten(), line=dict(color='green'), name='B beats C', legendgroup=2))
fig.add_trace(go.Scatter(y=pa.T[0][2].flatten(), line=dict(color='green'), opacity=0.5, showlegend=False, legendgroup=2))

fig.show()

## Naive Elo

In [58]:
def run_games_three_players(p, games_players, games_results, K=10, thres=0.10, stop_burnout=False):
    N = games_results.shape

    # Calculate Ratings
    coordinate_base = np.array([range(N[1])] * 2).T.flatten()
    players = [0, 1, 2]
    Ra = np.zeros([*N, 3])
    pa = np.zeros([*N, 3])
    pa[0] += 1/2
    finished_burnout = np.array([False] * N[1])
    n_to_convergence = np.ones(N[1]) * (N[0] + 1)
    for i in range(1, N[0]):
        # Set up players in game
        players_i = np.array([[0,1], [0,2], [1,2]])[games_players[i - 1]]
        Ra_coordinates = [coordinate_base, players_i.flatten()]
        pa_coordinates = [[0, 1] * N[1], coordinate_base, np.array([games_players[i - 1], games_players[i - 1]]).T.flatten()]

        # Update rating
        Sa_i = np.array([games_results[i - 1], 1 - games_results[i - 1]]).T.flatten()
        pa_i = np.array([pa[i - 1], 1 - pa[i - 1]])[*pa_coordinates]
        Ra[i] = Ra[i - 1].copy()
        Ra[i][*Ra_coordinates] += K * (Sa_i - pa_i)

        # Update Approx Probabilities
        pa[i] = np.apply_along_axis(
                    lambda x: [
                        calculate_probability(x[0], x[1]),
                        calculate_probability(x[0], x[2]), 
                        calculate_probability(x[1], x[2])
                    ],
                    1, 
                    Ra[i]
                )

        # Check if burnout is finished
        if not all(finished_burnout):
            condition = abs(pa[i].T - p[players, [i]]) <= p[players, [i]] * thres
            condition = condition.T.all(axis=1)
            finished_burnout = np.where(condition, True, finished_burnout)
            n_to_convergence = np.where(finished_burnout, n_to_convergence, i + 1)
            
            if all(finished_burnout) and stop_burnout: break

    return abs(np.transpose(p, [1, 2, 0]) - pa), n_to_convergence

In [62]:
N = [3000, 1000]
p, games_players, games_results = stable_three_player_generator(initials=[1/4, 3/4], N=N)

p_diff, n_to_convergence = run_games_three_players(p, games_players, games_results)
p_diff = np.transpose(p_diff, [2, 0, 1])

fig = go.Figure(layout=layout_dict)

group = 0
colors = ['blue', 'red', 'green']
x_range = list(range(N[0])) + list(reversed(range(N[0])))
for C2_players in p_diff:
    quantiles = np.apply_along_axis(lambda x: np.quantile(x, [0.1, 0.5, 0.9]), 1, C2_players).T
    fig.add_trace(go.Scatter(
        x = x_range, y=list(quantiles[2]) + list(quantiles[0][::-1]), fill='toself', mode='none',
        hoveron='points', fillcolor=colors[group], name=f'Match {group}', legendgroup=group, opacity=0.5
    ))
    fig.add_trace(go.Scatter(y=quantiles[1], line=dict(color=colors[group]), legendgroup=group, showlegend=False, name=f'Match {group} median'))
    group += 1

fig.update_yaxes(range=[0, 1])
fig.show()


## Improved

In [12]:

def run_games_three_players_improved(p, games_players, games_results, K_interval=[0,200], K_default=180, window=50, thres=0.10, stop_burnout=False):
    N = games_results.shape

    # Calculate Ratings
    coordinate_base = np.array([range(N[1])] * 2).T.flatten()
    players = [0, 1, 2]
    Ra = np.zeros([*N, 3])
    pa = np.zeros([*N, 3])
    pa[0] += 1/2
    finished_burnout = np.array([False] * N[1])
    n_to_convergence = np.ones(N[1]) * (N[0] + 1)
    K = K_generator(K_interval=K_interval, K_default=K_default)
    for i in range(1, N[0]):
        # Calculate heuristic
        window_list = [max(0, i - window), min(N[0], i + window)]
        frequentist_pa = three_player_heuristic(games_players[window_list[0]: window_list[1]], games_results[window_list[0]: window_list[1]]).T
        K_i = np.choose(games_players[i - 1], K(abs(pa[i - 1] - frequentist_pa)).T)


        # Set up players in game
        players_i = np.array([[0,1], [0,2], [1,2]])[games_players[i - 1]]
        Ra_coordinates = [coordinate_base, players_i.flatten()]
        pa_coordinates = [[0, 1] * N[1], coordinate_base, np.array([games_players[i - 1], games_players[i - 1]]).T.flatten()]

        # Update rating
        Sa_i = np.array([games_results[i - 1], 1 - games_results[i - 1]]).T.flatten()
        pa_i = np.array([pa[i - 1], 1 - pa[i - 1]])[*pa_coordinates]
        Ra[i] = Ra[i - 1].copy()
        Ra[i][*Ra_coordinates] += (K_i * (Sa_i - pa_i).reshape([N[1],-1]).T).T.flatten()

        # Update Approx Probabilities
        pa[i] = np.apply_along_axis(
                    lambda x: [
                        calculate_probability(x[0], x[1]),
                        calculate_probability(x[0], x[2]), 
                        calculate_probability(x[1], x[2])
                    ],
                    1, 
                    Ra[i]
                )

        # Check if burnout is finished
        if not all(finished_burnout):
            condition = abs(pa[i].T - p[players, [i]]) <= p[players, [i]] * thres
            condition = condition.T.all(axis=1)
            finished_burnout = np.where(condition, True, finished_burnout)
            n_to_convergence = np.where(finished_burnout, n_to_convergence, i + 1)
            
            if all(finished_burnout) and stop_burnout: break

    return abs(np.transpose(p, [1, 2, 0]) - pa), n_to_convergence

In [60]:
N = [3000, 1000]
p, games_players, games_results = stable_three_player_generator(initials=[1/4, 3/4], N=N)

p_diff, n_to_convergence = run_games_three_players_improved(p, games_players, games_results)
p_diff = np.transpose(p_diff, [2, 0, 1])



fig = go.Figure(layout=layout_dict)

group = 0
colors = ['blue', 'red', 'green']
x_range = list(range(N[0])) + list(reversed(range(N[0])))
for C2_players in p_diff:
    quantiles = np.apply_along_axis(lambda x: np.quantile(x, [0.1, 0.5, 0.9]), 1, C2_players).T
    fig.add_trace(go.Scatter(
        x = x_range, y=list(quantiles[2]) + list(quantiles[0][::-1]), fill='toself', mode='none',
        hoveron='points', fillcolor=colors[group], name=f'Match {group}', legendgroup=group, opacity=0.5
    ))
    fig.add_trace(go.Scatter(y=quantiles[1], line=dict(color=colors[group]), legendgroup=group, showlegend=False, name=f'Match {group} median'))
    group += 1

fig.update_yaxes(range=[0, 1])
fig.show()